In [1]:
import geopandas as gpd
import pandas as pd
import math
import ee
import geemap

In [2]:
ee.Authenticate()
ee.Initialize(project='ee-curuai')

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Import image collections

Landsat 7 - PY6S

In [4]:
landsat7 = ee.ImageCollection("projects/ee-curuai/assets/Py6S/LD7/ld7_py6s")\
            .select([ 'B1', 'B2', 'B3', 'B4', 'B5', 'B7'])
print(ee.Date(landsat7.first().get('system:time_start')).format().getInfo())
print(ee.Date(landsat7.sort('system:time_start',False).first().get('system:time_start')).format().getInfo())

2013-05-12T13:44:05
2017-09-28T13:50:48


Landsat 8 PY6S

In [5]:
landsat8 = (ee.ImageCollection("projects/ee-curuai/assets/Py6S/LD8/ld8_py6s")
            .select(['B2', 'B3', 'B4', 'B5', 'B6', 'B7']))
print(ee.Date(landsat8.first().get('system:time_start')).format().getInfo())
print(ee.Date(landsat8.sort('system:time_start',False).first().get('system:time_start')).format().getInfo())

2013-05-20T13:50:14
2017-09-27T13:54:12


# Transform into remote sensing reflectance and sunglint correction

In [6]:
def deglint (img):
  '''#dividir imagem corrigida por pi
  Rrs_sat_ac = Rsat_ac / pi
  fazer deglint
  Rrs_sat_ac_deglint(VNIR) = Rrs_sat_ac (VNIR) − Rrs_sat_ac (SWIR)
  correção no artigo INPE CURUAI'''
  Rrs = img.divide(math.pi)
  deglint = Rrs.select(['blue_mean','green_mean','red_mean','nir_mean','swir1','swir2'])\
    .subtract(Rrs.select('swir1'))

  return (deglint.updateMask(deglint.select(['red_mean']).gt(0)).updateMask(deglint.select(['blue_mean']).gt(0)).updateMask(deglint.select(['green_mean']).gt(0)).updateMask(deglint.select(['nir_mean']).gt(0))
          .copyProperties(img,['system:time_start','CLOUD_COVER',"system:index"]))

## Padronize band names

In [7]:
name_bands = ['blue_mean','green_mean','red_mean','nir_mean','swir1','swir2']

Landsat 7

In [8]:
#renomear bandas

ld7 = landsat7.map(lambda img: img.rename(name_bands)).map(deglint)
ld7.first()

Landsat 8

In [9]:
ld8 = landsat8.map(lambda img: img.rename(name_bands)).map(deglint)
ld8

# Mask land

In [10]:
# // Function to select water pixels
def hsvComposite (image):
  composite = image.select(['blue_mean','green_mean','red_mean']).rgbToHsv()#.clip(limits);
  hue = composite.select("hue");
  max_mask = hue.lte(0.9)
  min_mask = hue.gte(0.3)
  return image.updateMask(max_mask).updateMask(min_mask);

In [11]:
ld8_masked = ld8.map(hsvComposite)
ld7_masked = ld7.map(hsvComposite)
ld8_masked

# Import Model and Classify Images

In [12]:
classifier = ee.Classifier.load('projects/ee-curuai/assets/RF_regressor')
classifier

In [13]:
predictors = ['blue_mean', 'green_mean','red_mean', 'nir_mean']
ld7_classified = ld7_masked.select(predictors).map(lambda img: img.classify(classifier=classifier).copyProperties(img,['system:index','system:time_start']))
ld7_classified

In [14]:
ld8_classified = ld8_masked.select(predictors).map(lambda img: img.classify(classifier=classifier).copyProperties(img,['system:index','system:time_start']))
ld8_classified

# Import Points

In [58]:
# points used for regression
reg_points = geemap.geojson_to_ee('/content/drive/MyDrive/CURUAI_PROCESS/regression_p.geojson')
reg_points_unique = reg_points.distinct('.geo')
reg_points_unique


# Sample images from regression points

In [59]:
projection = ld8.first().select('red_mean').projection()

In [67]:
ld7_sample = (ld7_classified
              .map(lambda img: img.addBands(ee.Image(ee.Number(img.get('system:time_start')))).rename(['SPM_img','img_date']))
              .map(lambda img: img.sampleRegions(collection = reg_points_unique, scale=30, projection=projection,geometries=False))
              .flatten()
              .map(lambda feat: feat.set('img_datetime',ee.Date(feat.get('img_date')).format('yyyy-MM-dd HH:mm:ss'))))
ld7_sample.select(['SPM_img','img_datetime']).limit(10)

In [68]:
ld8_sample = (ld8_classified
              .map(lambda img: img.addBands(ee.Image(ee.Number(img.get('system:time_start')))).rename(['SPM_img','img_date']))
              .map(lambda img: img.sampleRegions(collection = reg_points_unique, scale=30, projection=projection,geometries=False))
              .flatten()
              .map(lambda feat: feat.set('img_datetime',ee.Date(feat.get('img_date')).format('yyyy-MM-dd HH:mm:ss'))))
ld8_sample.select(['SPM_img','img_datetime']).size()

In [71]:
obs_points = geemap.ee_to_df(reg_points)


In [72]:
ld8_pred = ee.data.computeFeatures({
    'expression': ld8_sample.select(['SPM_img','img_datetime']),
    'fileFormat': 'PANDAS_DATAFRAME'
})

In [73]:
ld7_pred = ee.data.computeFeatures({
    'expression': ld7_sample.select(['SPM_img','img_datetime']),
    'fileFormat': 'PANDAS_DATAFRAME'
})

In [76]:
ld7_pred = ld7_pred.astype({'SPM_img': 'float64'})
ld8_pred = ld8_pred.astype({'SPM_img': 'float64'})

LATITUDE  LONGITUDE   SPM  SPM_predicted WATER_PERIOD  blue_mean  \
0 -2.196960 -55.299530  34.4      54.698376            R   0.016988   
1 -2.221738 -55.270194  44.4      47.285001            R   0.017570   
2 -2.209570 -55.347110  44.8      36.468949            R   0.014560   
3 -2.262023 -55.456187  45.2      65.154042            R   0.031565   
4 -2.133265 -55.488798  39.2      44.829901            R   0.021785   

              datetime  green_mean  nir_mean  red_mean  
0  2013-03-09 11:20:00    0.027905  0.016161  0.036151  
1  2013-03-09 13:00:00    0.029232  0.013234  0.034852  
2  2013-03-09 14:35:00    0.020075  0.010206  0.024131  
3  2013-03-11 08:00:00    0.039040  0.020332  0.043538  
4  2013-03-11 13:00:00    0.032779  0.014011  0.038842

In [74]:
import seaborn as sns
sns.lineplot(data=ld8_pred, x ='datetime',y= 'img_datetime',color='gray')
sns.lineplot(data=ld7_pred, x ='datetime',y= 'img_datetime',color='lightgray')
sns.pointplot(data=obs_points, x ='datetime',y= 'SPM', linestyle="none", markersize=5, alpha=.6,hue='WATER_PERIOD')

ValueError: Could not interpret value `datetime` for `x`. An entry with this name does not appear in `data`.

In [77]:
Map = geemap.Map(basemap='HYBRID')
roi_points = ee.FeatureCollection('projects/ee-curuai/assets/curuai_points')
Map.centerObject(roi_points,10)
imgld7 = ee.Filter.eq('system:index','BOA_LE07_228061_20130604')
imgld8 = ee.Filter.eq('system:index','BOA_LC08_228061_20140615')

Map.addLayer(ld7.filter(imgld7).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld7')
Map.addLayer(ld8.filter(imgld8).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld8')

Map.addLayer(ld7_masked.filter(imgld7).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld7 masked')
Map.addLayer(ld8_masked.filter(imgld8).first(), {'bands':['red_mean','green_mean','blue_mean'], 'min':0,'max':0.02}, 'ld8 masked')


Map.addLayer(ld7_classified.filter(imgld7).first(), {'palette':['#ffffb2','#fecc5c','#fd8d3c','#e31a1c'], 'min':0,'max':150}, 'classification LD7')
Map.addLayer(ld8_classified.filter(imgld8).first(), {'palette':['#ffffb2','#fecc5c','#fd8d3c','#e31a1c'], 'min':0,'max':150}, 'classification LD8')


Map.addLayer(roi_points, {'color':'darkred'}, 'Data polygon');
Map

Map(center=[-2.184599717160098, -55.49304633852027], controls=(WidgetControl(options=['position', 'transparent…